In [ ]:
from tqdm import tqdm
import numpy as np
import pandas as pd
import os
import librosa
import glob
import matplotlib.pyplot as plt

In [ ]:
path_list = sorted(glob.glob('/Users/yash/Downloads/downloaded_songs/*/*/*'))

In [ ]:
import librosa
import soundfile  # Use ffmpeg decoder
import numpy as np
sr = 22050
hop_length = 512
features_list = []
for path in tqdm(path_list):

    track = path.split('/')[7].split('.')[0]
    try:
        y, sr = librosa.load(path, sr=22050)

        stft = np.abs(librosa.stft(y)) # computing stft for our signal to further calculate chromagram
        onset_env = librosa.onset.onset_strength(y=y, sr=sr, hop_length=hop_length) # extracting onset_env to further calculate tempo and tempogram

        tempo = librosa.beat.tempo(onset_envelope=onset_env, sr=sr)
        tempogram = librosa.feature.tempogram(onset_envelope=onset_env, sr=sr,hop_length=hop_length)
        mean_tempogram = np.mean(librosa.feature.tempogram(onset_envelope=onset_env, sr=sr, hop_length=hop_length),axis=1)
        std_tempogram = np.std(librosa.feature.tempogram(onset_envelope=onset_env, sr=sr, hop_length=hop_length),axis=1)

        # normal_chromagram = librosa.feature.chroma_stft(y=y, sr=sr)
        mean_chromagram = np.mean(librosa.feature.chroma_stft(S=stft, sr=sr),axis=1)
        std_chromagram = np.std(librosa.feature.chroma_stft(S=stft, sr=sr),axis=1)

        # normal_tonnetz = np.mean(librosa.feature.tonnetz(y=librosa.effects.harmonic(X), sr=sample_rate).T,axis=0)
        mean_tonnetz = np.mean(librosa.feature.tonnetz(y=librosa.effects.harmonic(y), sr=sr),axis=1)
        std_tonnetz = np.std(librosa.feature.tonnetz(y=librosa.effects.harmonic(y), sr=sr),axis=1)

        features_list.append([track,onset_env,tempo,tempogram,mean_tempogram,std_tempogram,mean_chromagram,std_chromagram,mean_tonnetz,std_tonnetz])

    except:
        fails.append(path)

df_features = pd.DataFrame(features_list, columns=['track_id','onset_env','tempo','tempogram','mean_tempogram','std_tempogram','mean_chromagram','std_chromagram','mean_tonnetz','std_tonnetz'])
df_features.to_csv('./mean_std_features.csv')



  0%|          | 0/11180 [00:00<?, ?it/s]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 1/11180 [00:05<18:31:24,  5.97s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 2/11180 [00:10<16:36:53,  5.35s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 3/11180 [00:15<15:55:41,  5.13s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|      

In [35]:
df_features = pd.DataFrame(features_list, columns=['track_id','onset_env','tempo','tempogram','mean_tempogram','std_tempogram','mean_chromagram','std_chromagram','mean_tonnetz','std_tonnetz'])

In [23]:
fails_tempo = []
tempogram_features = []

Extracting Tempogram features again with a window length of 96

In [24]:
for path in tqdm(path_list):
    track = path.split('/')[7].split('.')[0]
    try:
        y, sr = librosa.load(path, sr=22050)
        stft = np.abs(librosa.stft(y)) # computing stft for our signal to further calculate chromagram
        onset_env = librosa.onset.onset_strength(y=y, sr=sr, hop_length=hop_length) # extracting onset_env to further calculate tempo and tempogram
        tempogram = librosa.feature.tempogram(onset_envelope=onset_env, sr=sr,hop_length=hop_length, win_length=96)
        mean_tempogram = np.mean(tempogram,axis=1)
        std_tempogram = np.std(tempogram,axis=1)
        tempogram_features.append([track,mean_tempogram,std_tempogram])

    except:
        fails_tempo.append(path)

tempogram_df = pd.DataFrame(tempogram_features, columns=['track_id','mean_tempogram','std_tempogram'])
tempogram_df.to_csv('./tempogram_features.csv') 

  0%|          | 0/11180 [00:00<?, ?it/s]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 1/11180 [00:01<4:18:06,  1.39s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 2/11180 [00:02<4:07:37,  1.33s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|          | 3/11180 [00:03<3:54:43,  1.26s/it]/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
  0%|         

In [28]:
np.save('./np_tempogram.npy',tempogram_features)

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/numpy/lib/npyio.py:528: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  arr = np.asanyarray(arr)


In [40]:
new_df_features = df_features.drop(['onset_env','tempogram','mean_tempogram','std_tempogram'],axis=1)

In [57]:
all_features = pd.merge(tempogram_df,new_df_features,on='track_id')
np.save('./all_features.npy',all_features)